# Structure object

The `AbiPy` structure inherits from the `pymatgen` structure.
One has therefore access to all the methods and tools already available in `pymatgen`.
In this notebook, we mainly focus on the extensions added by `AbiPy`.
For the features provided by pymatgen, please consult the
[official pymatgen documentation](http://pymatgen.org/usage.html#structures-and-molecules).

{{ Structure }} and {{ pymatgen_Structure}}

In [1]:
import warnings
warnings.filterwarnings("ignore") # to get rid of deprecation warnings

# Import abipy modules
from abipy import abilab
from abipy.abilab import Structure
import abipy.data as abidata

# Useful tools we'll need later on.
from pprint import pprint
import numpy as np

# This line configures matplotlib to show figures embedded in the notebook.
# Replace `inline` with `notebook` in classic notebook
%matplotlib inline

# Option available in jupyterlab. See https://github.com/matplotlib/jupyter-matplotlib
#%matplotlib widget

## Reading a structure from file

It is possible to initialize a structure object from different file formats:

   * CIF
   * POSCAR/CONTCAR
   * CHGCAR
   * LOCPOT,
   * vasprun.xml
   * CSSR
   * ABINIT Netcdf files
   * pymatgen's JSON serialized structures

Note, in particular, that one can initialize the structure from the netcdf files
produced by Abinit (`GSR.nc`, `WFK.nc`, etc) as well as output files in text format
such as the Abinit input/output files or even the DDB file.

To initialize the structure from a CIF file use the `from_file` method:

In [2]:
structure = Structure.from_file(abidata.cif_file("si.cif"))
print(structure)

Full Formula (Si2)
Reduced Formula: Si
abc   :   3.866975   3.866975   3.866975
angles:  60.000000  60.000000  60.000000
pbc   :       True       True       True
Sites (2)
  #  SP       a     b     c
---  ----  ----  ----  ----
  0  Si    0     0     0
  1  Si    0.25  0.25  0.25


```{include} snippets/abidata_note.md
```

To read the structure from an Abinit netcdf file, use:

In [3]:
structure = Structure.from_file(abidata.ref_file("si_nscf_GSR.nc"))

print(structure.to_string(verbose=1))  # Use to_string with verbose > 0 to get more info

Full Formula (Si2)
Reduced Formula: Si
abc   :   3.866975   3.866975   3.866975
angles:  60.000000  60.000000  60.000000

Spglib space group info (magnetic symmetries not taken into account).
Spacegroup: Fd-3m (227), Hall: F 4d 2 3 -1d, Abinit spg_number: 227
Crystal_system: cubic, Lattice_type: cubic, Point_group: m-3m

  Idx  Symbol    Reduced_Coords              Wyckoff      EqIdx
-----  --------  --------------------------  ---------  -------
    0  Si        +0.00000 +0.00000 +0.00000  (2a)             0
    1  Si        +0.25000 +0.25000 +0.25000  (2a)             0

Abinit Spacegroup: spgid: 227, num_spatial_symmetries: 48, has_timerev: True, symmorphic: True


/usr/share/miniconda/envs/abipy/lib/python3.12/site-packages/spglib/spglib.py:115: DeprecationWarning: dict interface (SpglibDataset['wyckoffs']) is deprecated.Use attribute interface ({self.__class__.__name__}.{key}) instead
  warnings.warn(
/usr/share/miniconda/envs/abipy/lib/python3.12/site-packages/spglib/spglib.py:115: DeprecationWarning: dict interface (SpglibDataset['equivalent_atoms']) is deprecated.Use attribute interface ({self.__class__.__name__}.{key}) instead
  warnings.warn(


Use `to_abivars` to get a python dictionary with the list of Abinit variables.

In [4]:
structure.to_abivars()

{'natom': 2,
 'ntypat': 1,
 'typat': array([1, 1]),
 'znucl': [14],
 'xred': array([[0.  , 0.  , 0.  ],
        [0.25, 0.25, 0.25]]),
 'acell': [1.0, 1.0, 1.0],
 'rprim': array([[6.32850055, 0.        , 3.6537615 ],
        [2.10950018, 5.96656754, 3.6537615 ],
        [0.        , 0.        , 7.30752299]])}

and the `abi_string` property to get a string that can be used directly in the input file:

In [5]:
print(structure.abi_string)

 natom 2
 ntypat 1
 typat 1 1
 znucl 14
 xred
    0.0000000000    0.0000000000    0.0000000000
    0.2500000000    0.2500000000    0.2500000000
 acell    1.0    1.0    1.0
 rprim
    6.3285005521    0.0000000000    3.6537614973
    2.1095001840    5.9665675402    3.6537614973
    0.0000000000    0.0000000000    7.3075229946


To visualize the structure with matplotlib, use:

In [6]:
structure.plot();

AttributeError: 'Arrow3D' object has no attribute 'do_3d_projection'

<Figure size 640x480 with 1 Axes>

The matplotlib version is minimalistic but it plays well with jupyter notebooks.
For a more advanced visualization we suggest using a specialized graphical applications.
Fortunately, one can invoke external applications directly from AbiPy with e.g.

In [7]:
# structure.visualize("vesta")

provided VESTA is already installed on your machine and the binary can be found in  **$PATH**.

To get a structure from the [materials project database](https://www.materialsproject.org), use:

In [8]:
# Remember to set the env variable PMG_MAPI_KEY in your ~/.pmgrc.yaml files.
si2_mp = Structure.from_mpid("mp-149")
print(si2_mp)

ValueError: Please supply an API key. See https://materialsproject.org/api for details.

In some cases, we have multiple structures and we need to compare the lattice parameters.
Use `dataframes_from_structures` to build a pandas DataFrame:

In [ ]:
dfs = abilab.dataframes_from_structures([structure, si2_mp], index=["CIF", "MP"])

then we can compare the lattice parameters with:

In [ ]:
dfs.lattice

Note that all AbiPy robots have this feature built-in.
Sometimes it is much easier to build a robot directly from files
and then compare the structures with e.g. `robot.get_lattice_dataframe()`.


## Converting to other formats

Use `structure.convert(format)` to get the string representation in the new format:

In [ ]:
for fmt in ("cif", "POSCAR", "qe"):
    print((" Abinit --> %s " % fmt).center(80, "*"))
    print(structure.convert(fmt=fmt))

## Getting info on the structure

In [ ]:
print(structure.reciprocal_lattice)

In [ ]:
structure.reciprocal_lattice.matrix.T @ structure.lattice.matrix / (2 * np.pi)

In [ ]:
# List of high-symmetry k-points.
print(structure.hsym_kpoints)

The method `calc_ksampling` allows one to get an efficient sampling of the Brillouin zone
by just specifying the number of divisions to be used for the smallest lattice vector of the reciprocal lattice:

In [ ]:
pprint(structure.calc_ksampling(nksmall=10))

To get the recommended high symmetry $k$-path in reduced coordinates:

In [ ]:
structure.calc_kptbounds()

The high-symmetry **q**-path is automatically selected assuming
the structure fulfills the convention described in [Setyawan2010](https://doi.org/10.1016/j.commatsci.2010.05.010)

To visualize the Brillouin zone with matplotlib, use:

In [ ]:
structure.plot_bz();

For the plotly version, use:

In [ ]:
structure.plotly_bz();

```{note}
The name of the plotly method (if implemented) is obtained by replacing the `plot` verb with `plotly`.
```

To get the number of valence electrons for a given set of pseudopotentials:

In [ ]:
structure.num_valence_electrons(pseudos=abidata.pseudos("14si.pspnc"))

To visualize the X-ray diffraction plot with pymatgen XRDCalculator, use:

In [ ]:
structure.plot_xrd();

## The `abistruct.py` script

The {{ abistruct }} script provides a handy command line
interface to operate on structure objects constructed from external files.
There are several options available as well an interface to the {{ materials project }}
and the {{ COD }} database.

To obtain the list of available commands, use:

In [ ]:
!abistruct.py --help

## Creating a GUI inside a notebook

Several AbiPy objects provide a `get_panel` method that allows one to create a {{ panel }} GUI
exposing some of the underlying AbiPy methods.
Similar capabilities are also available via the {{ abipygui }} web app.

To build a panel GUI for a given structure use:

In [ ]:
abilab.abipanel()
structure.get_panel()